In [ ]:
import requests
class DownloadEnamine:
    """
    This class is set up to download Enamine REAL database on a remote machine.
    Instatiation requires plain ``username`` and ``password``.

    .. code-block::python
        de = DownloadEnamine('foo.bar@baz.ac.uk', 'Foo123')
        de.download_all('REAL')

    Note, this is copied off the route of the web page and not the Enamine Store API.
    Plus the official documentation (emailed Word document) is for the old Store and
    no longer applies anyway (plain text username and password in GET header "Authorization").

    The URLs pointing to the download pages were copied off manually.
    """
    REAL=[
    '2024.07_Enamine_REAL_HAC_25_1B_CXSMILES.cxsmiles.bz2',
    ]
    LOGIN_URL = 'https://enamine.net/compound-collections/real-compounds/real-database'

    def __init__(self, username, password):
        self.sesh = requests.Session()
        login_payload = {
            'username': username,
            'password': password,
            'Submit': 'Login',
            'remember': 'yes',
            'option': 'com_users',
            'task': 'user.login'
        }
        self.sesh.headers.update({'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'})
        response = self.sesh.post(self.LOGIN_URL, data=login_payload)
        response.raise_for_status()

        print("Login appears successful.")

    def download_all(self, catalogue='REAL'):
        """
        The URLs of the databases files are in the class attribute of that same catalogue name (i.e. ``REAL``).
        """
        for filename in getattr(self, catalogue):
            self.download('REAL', filename)

    def check(self, catalogue='REAL'):
        for filename in getattr(self, catalogue):
            with self.sesh.get(f'https://ftp.enamine.net/download/{catalogue}/{filename}', stream=True) as r:
                r.raise_for_status()  # requests.exceptions.HTTPError
                for chunk in r.iter_content(chunk_size=8192):
                    break

    def download(self, catalogue, filename):
        """
        Downloads the ``filename`` of the given ``catalogue``
        """
        with self.sesh.get(f'https://ftp.enamine.net/download/{catalogue}/{filename}', stream=True) as r:
            r.raise_for_status()
            with open(filename, 'wb') as f:
                for chunk in r.iter_content(chunk_size=8192):
                    f.write(chunk)


real_download = DownloadEnamine('taitdang@stanford.edu', 'Z!6CJd2BjQs!y4x')
real_download.download_all('REAL')

In [ ]:
!source /lfs/skampere1/0/sttruong/miniconda3/etc/profile.d/conda.sh

In [ ]:
export LD_LIBRARY_PATH="/lfs/skampere1/0/sttruong/cheapvs_llm/Vina-GPU-2.1/AutoDock-Vina-GPU-2.1/boost_1_77_0/stage/lib:${LD_LIBRARY_PATH}"

In [ ]:
conda install jupyter ipykernel
python -m ipykernel install --user --name cheapvs_llm --display-name "Python (cheapvs_llm)"


In [1]:
import csv
import os
import sys

# --- Configuration ---
input_smiles_file = "smiles_sampled_20k.txt"  # <-- Your input SMILES text file
output_csv_file = "lig_llm.csv"   # <-- Your desired output CSV filename
csv_column_name = "SMILES"                   # <-- The header for the column in the CSV
# --- End Configuration ---

# --- Script Start ---

# Check if input file exists
if not os.path.isfile(input_smiles_file):
    print(f"ERROR: Input file not found: {input_smiles_file}")
    sys.exit(1)

print(f"Reading SMILES from: {input_smiles_file}")
print(f"Writing CSV with column '{csv_column_name}' to: {output_csv_file}")
print("-" * 30)

count_success = 0
count_skipped = 0

try:
    # Open the input text file for reading ('r')
    # Open the output CSV file for writing ('w')
    # newline='' is important to prevent blank rows being inserted by csv.writer
    with open(input_smiles_file, 'r') as infile, \
         open(output_csv_file, 'w', newline='') as outfile:

        # Create a CSV writer object
        csv_writer = csv.writer(outfile)

        # Write the header row
        csv_writer.writerow([csv_column_name])

        # Process each line in the input file
        for i, line in enumerate(infile):
            smiles_string = line.strip() # Remove leading/trailing whitespace (including newline)

            if not smiles_string: # Skip empty lines
                print(f"Warning: Skipped empty line at line number {i+1}")
                count_skipped += 1
                continue

            # Write the SMILES string as a row in the CSV
            # writerow expects an iterable (like a list), even for a single column
            csv_writer.writerow([smiles_string])
            count_success += 1

except IOError as e:
    print(f"ERROR: Could not open or write file. Details: {e}")
    sys.exit(1)
except Exception as e:
    # Catch any other unexpected errors during processing
    print(f"An unexpected error occurred processing line {i+1}: {e}")
    sys.exit(1)


print("-" * 30)
print(f"Processing finished.")
print(f"Successfully wrote: {count_success} SMILES strings to CSV.")
if count_skipped > 0:
    print(f"Skipped empty lines: {count_skipped}")
print(f"Output CSV written to: {output_csv_file}")

Reading SMILES from: smiles_sampled_20k.txt
Writing CSV with column 'SMILES' to: lig_llm.csv
------------------------------
------------------------------
Processing finished.
Successfully wrote: 20354 SMILES strings to CSV.
Output CSV written to: lig_llm.csv


In [10]:
from admet_ai import ADMETModel
import numpy as np
import pandas as pd
from rdkit import Chem
from rdkit.Chem import (
    QED,
    Crippen,
    Descriptors,
    Lipinski,
    MolSurf,
    RDConfig,
    AllChem,
    rdMolDescriptors as rdmd,
)
from rdkit.Chem.rdMolDescriptors import CalcFractionCSP3
from rdkit.DataStructs import TanimotoSimilarity
from scipy.stats import norm
from pandarallel import pandarallel
sys.path.append(os.path.join(RDConfig.RDContribDir, "SA_Score"))
import sascorer

def add_property_columns(df_in):
    pandarallel.initialize(progress_bar=False, nb_workers=12)
    model = ADMETModel(include_physchem=False, num_workers=12)
    """Add property columns to the DataFrame using pandarallel."""
    # Convert SMILES to RDKit Mol objects
    df_in["Mol"] = df_in["SMILES"].parallel_apply(lambda x: Chem.MolFromSmiles(x))
    AliphaticRings = Chem.MolFromSmarts("[$([A;R][!a])]")
    df_in["MW"] = df_in["Mol"].parallel_apply(Descriptors.MolWt)
    df_in["LogP"] = df_in["Mol"].parallel_apply(Crippen.MolLogP)
    df_in["numHDonors"] = df_in["Mol"].parallel_apply(Lipinski.NumHDonors)
    df_in["numHAcceptors"] = df_in["Mol"].parallel_apply(Lipinski.NumHAcceptors)
    df_in["TPSA"] = df_in["Mol"].parallel_apply(MolSurf.TPSA)
    df_in["rotBonds"] = df_in["Mol"].parallel_apply(
        lambda mol: rdmd.CalcNumRotatableBonds(
            mol, rdmd.NumRotatableBondsOptions.Strict
        )
    )
    df_in["Arom"] = df_in["Mol"].parallel_apply(
        lambda mol: len(
            Chem.GetSSSR(Chem.DeleteSubstructs(Chem.Mol(mol), AliphaticRings))
        )
    )
    df_in["QED"] = df_in["Mol"].parallel_apply(QED.qed)
    df_in["SA"] = df_in["Mol"].parallel_apply(sascorer.calculateScore)
    df_in["FractionCSP3"] = df_in["Mol"].parallel_apply(
        lambda mol: CalcFractionCSP3(mol)
    )

    admet_predictions = model.predict(smiles=df_in["SMILES"].values)
    properties = ['Lipinski', 'stereo_centers', 'AMES', 'BBB_Martins', 'Bioavailability_Ma', 'CYP1A2_Veith', 'CYP2C19_Veith', 'CYP2C9_Substrate_CarbonMangels', 'CYP2C9_Veith', 'CYP2D6_Substrate_CarbonMangels', 'CYP2D6_Veith', 'CYP3A4_Substrate_CarbonMangels', 'CYP3A4_Veith', 'Carcinogens_Lagunin', 'ClinTox', 'DILI', 'HIA_Hou', 'NR-AR-LBD', 'NR-AR', 'NR-AhR', 'NR-Aromatase', 'NR-ER-LBD', 'NR-ER', 'NR-PPAR-gamma', 'PAMPA_NCATS', 'Pgp_Broccatelli', 'SR-ARE', 'SR-ATAD5', 'SR-HSE', 'SR-MMP', 'SR-p53', 'Skin_Reaction', 'hERG', 'Caco2_Wang', 'Clearance_Hepatocyte_AZ', 'Clearance_Microsome_AZ', 'Half_Life_Obach', 'HydrationFreeEnergy_FreeSolv', 'LD50_Zhu', 'Lipophilicity_AstraZeneca', 'PPBR_AZ', 'Solubility_AqSolDB', 'VDss_Lombardo', 'Lipinski_drugbank_approved_percentile', 'stereo_centers_drugbank_approved_percentile', 'tpsa_drugbank_approved_percentile', 'AMES_drugbank_approved_percentile', 'BBB_Martins_drugbank_approved_percentile', 'Bioavailability_Ma_drugbank_approved_percentile', 'CYP1A2_Veith_drugbank_approved_percentile', 'CYP2C19_Veith_drugbank_approved_percentile', 'CYP2C9_Substrate_CarbonMangels_drugbank_approved_percentile', 'CYP2C9_Veith_drugbank_approved_percentile', 'CYP2D6_Substrate_CarbonMangels_drugbank_approved_percentile', 'CYP2D6_Veith_drugbank_approved_percentile', 'CYP3A4_Substrate_CarbonMangels_drugbank_approved_percentile', 'CYP3A4_Veith_drugbank_approved_percentile', 'Carcinogens_Lagunin_drugbank_approved_percentile', 'ClinTox_drugbank_approved_percentile', 'DILI_drugbank_approved_percentile', 'HIA_Hou_drugbank_approved_percentile', 'NR-AR-LBD_drugbank_approved_percentile', 'NR-AR_drugbank_approved_percentile', 'NR-AhR_drugbank_approved_percentile', 'NR-Aromatase_drugbank_approved_percentile', 'NR-ER-LBD_drugbank_approved_percentile', 'NR-ER_drugbank_approved_percentile', 'NR-PPAR-gamma_drugbank_approved_percentile', 'PAMPA_NCATS_drugbank_approved_percentile', 'Pgp_Broccatelli_drugbank_approved_percentile', 'SR-ARE_drugbank_approved_percentile', 'SR-ATAD5_drugbank_approved_percentile', 'SR-HSE_drugbank_approved_percentile', 'SR-MMP_drugbank_approved_percentile', 'SR-p53_drugbank_approved_percentile', 'Skin_Reaction_drugbank_approved_percentile', 'hERG_drugbank_approved_percentile', 'Caco2_Wang_drugbank_approved_percentile', 'Clearance_Hepatocyte_AZ_drugbank_approved_percentile', 'Clearance_Microsome_AZ_drugbank_approved_percentile', 'Half_Life_Obach_drugbank_approved_percentile', 'HydrationFreeEnergy_FreeSolv_drugbank_approved_percentile', 'LD50_Zhu_drugbank_approved_percentile', 'Lipophilicity_AstraZeneca_drugbank_approved_percentile', 'PPBR_AZ_drugbank_approved_percentile', 'Solubility_AqSolDB_drugbank_approved_percentile', 'VDss_Lombardo_drugbank_approved_percentile']
    for prop in properties:
        df_in[prop] = admet_predictions[prop].values
    # Apply rounding
    df_in = df_in.drop(columns=["Mol"])
    cols = df_in.columns
    df_in[cols] = df_in[cols].round(3)

    return df_in


def process_and_save_molecules(input_file, output_file):
    # Load input file
    df = (
        pd.read_csv(input_file)
        if input_file.endswith(".csv")
        else pd.read_parquet(input_file)
    )

    # Add molecular properties
    df = add_property_columns(df)

    # Save output file
    if output_file.endswith(".csv"):
        df.to_csv(output_file, index=False)
    elif output_file.endswith(".parquet"):
        df.to_parquet(output_file, index=False)
    else:
        raise ValueError("Output file must be .csv or .parquet")

    print(f"Processed DataFrame saved to: {output_file}")
    
# process_and_save_molecules('/lfs/skampere1/0/sttruong/cheapvs_llm/lig_llm.csv', '/lfs/skampere1/0/sttruong/cheapvs_llm/lig_llm_prop.csv')

In [12]:
import pandas as pd

files = os.listdir('/lfs/skampere1/0/sttruong/cheapvs_llm/20_targets/drugs_filtered/')
for file in files:
    if file.endswith('.csv'):
        df = pd.read_csv(f'/lfs/skampere1/0/sttruong/cheapvs_llm/20_targets/drugs_filtered/{file}')
        df = add_property_columns(df)
        name = file.split('.')[0] + '_prop.csv'
        df.to_csv(f'/lfs/skampere1/0/sttruong/cheapvs_llm/20_targets/drugs_filtered/{file}', index=False)

INFO: Pandarallel will run on 12 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.


/lfs/local/0/sttruong/miniconda3/envs/cheapvs_llm/lib/python3.10/site-packages/chemprop/utils.py:473: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  vars(torch.load(path, map

Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained parameter "readout.4.bias".
Moving model to cuda
Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained p

/lfs/local/0/sttruong/miniconda3/envs/cheapvs_llm/lib/python3.10/site-packages/chemprop/utils.py:418: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state = torch.load(path, 

Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained parameter "readout.4.bias".
Moving model to cuda
Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained p

...

model ensembles:   0%|          | 0/2 [00:00<?, ?it/s]














model ensembles:  50%|█████     | 1/2 [00:04<00:04,  4.41s/it]














model ensembles: 100%|██████████| 2/2 [00:08<00:00,  4.24s/it]
/lfs/local/0/sttruong/miniconda3/envs/cheapvs_llm/lib/python3.10/site-packages/chemprop/utils.py:473: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start s

INFO: Pandarallel will run on 12 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.
Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained parameter "readout.4.bias".
Moving model to cuda
Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained par

/lfs/local/0/sttruong/miniconda3/envs/cheapvs_llm/lib/python3.10/site-packages/chemprop/utils.py:418: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state = torch.load(path, 

Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained parameter "readout.4.bias".
Moving model to cuda
Loading pretrained parameter "encoder.encoder.0.cached_zero_vector".
Loading pretrained parameter "encoder.encoder.0.W_i.weight".
Loading pretrained parameter "encoder.encoder.0.W_h.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.weight".
Loading pretrained parameter "encoder.encoder.0.W_o.bias".
Loading pretrained parameter "readout.1.weight".
Loading pretrained parameter "readout.1.bias".
Loading pretrained parameter "readout.4.weight".
Loading pretrained p

model ensembles:   0%|          | 0/2 [00:00<?, ?it/s]














model ensembles:  50%|█████     | 1/2 [00:04<00:04,  4.91s/it]














model ensembles: 100%|██████████| 2/2 [00:10<00:00,  5.09s/it]


In [ ]:
import pandas as pd

df_20k = pd.read_csv('lig_llm_prop.csv')
df_drug = pd.read_csv('20_targets/drugs_filtered/PDE4A_HUMAN.csv')
combined_df = pd.concat([df_20k, df_drug], ignore_index=True)


In [23]:
combined_df

SMILES       MW   LogP  \
0                 COc1cc(C=Cc2nc(-c3ccccc3)cs2)ccc1OCC#N  348.427  4.891   
1            COc1ccn2c(C=C(C#N)C(=O)c3ccc(Cl)cc3F)cnc2c1  355.756  3.925   
2               C#CCOc1ccc(C=C(Cl)c2nc3ccc(C)cc3o2)cc1OC  353.805  4.894   
3            CC(Sc1nnc(-c2ccccc2Cl)n1N)c1ncc(C(C)(C)C)o1  377.901  4.451   
4             NC(=O)c1ccccc1OCC(=O)Nc1ccc(OC(F)F)c(Cl)c1  370.739  3.058   
...                                                  ...      ...    ...   
20364  COC1=CC=CC(NC2=C(C=NC3=C(C)C=C(C=C23)S(=O)(=O)...  518.595  3.929   
20365  CS(=O)(=O)NC1=CC2=C(OC3=C2C(=CC=C3OC(F)F)C(=O)...  516.309  5.513   
20366  [O-][N+]1=CC(=CC=C1)C#CC1=CC(=CC=C1)N1C=C(C(=O...  422.444  2.311   
20367  COC1=CC=C(C=C1OC1CCCC1)C(CC(N)=O)N1C(=O)C2=C(C...  408.454  3.229   
20368          OB1OCC2=C1C=CC(OC1=CC(C#N)=C(C=C1)C#N)=C2  276.060  1.440   

       numHDonors  numHAcceptors    TPSA  rotBonds  Arom    QED     SA  ...  \
0               0              5   55.14         6     3  0.636  2.317  ...   
1               0              5   67.39         4     3  0.404  2.755  ...   
2               0              4   44.49         5     3  0.612  2.612  ...   
3               1              7   82.76         4     3  0.534  3.167  ...   
4               2              4   90.65         7     2  0.783  1.962  ...   
...           ...            ...     ...       ...   ...    ...    ...  ...   
20364           2              7  131.69         7     4  0.379  2.571  ...   
20365           2              6  110.53         6     4  0.350  2.774  ...   
20366           1              5   90.93         3     4  0.312  2.887  ...   
20367           1              5   98.93         7     2  0.709  2.776  ...   
20368           1              5   86.27         2     2  0.838  2.894  ...   

       Half_Life_Obach_drugbank_approved_percentile  \
0                                            15.432   
1                                            62.389   
2                                            79.643   
3                                            15.859   
4                                            63.358   
...                                             ...   
20364                                        96.859   
20365                                        99.612   
20366                                        50.834   
20367                                        37.379   
20368                                        10.237   

       HydrationFreeEnergy_FreeSolv_drugbank_approved_percentile  \
0                                                 61.303           
1                                                 38.813           
2                                                 81.078           
3                                                 65.762           
4                                                 35.169           
...                                                  ...           
20364                                             18.457           
20365                                             26.871           
20366                                             34.122           
20367                                             60.256           
20368                                             54.323           

       LD50_Zhu_drugbank_approved_percentile  \
0                                     38.038   
1                                     84.878   
2                                     32.765   
3                                     26.289   
4                                     25.514   
...                                      ...   
20364                                 60.605   
20365                                 80.109   
20366                                 79.953   
20367                                 51.105   
20368                                 91.121   

       Lipophilicity_AstraZeneca_drugbank_approved_percentile  \
0                                                 95.812        
1  